In [23]:
# -*- coding: utf-8 -*-
"""
Created on Wed Feb  5 19:21:35 2025

@author: profa
"""

########################################
## 2021 - Gates
##
## Topics: 
    # Data gathering via API
    #  - URLs and GET
    # Cleaning and preparing text DATA
    # DTM and Data Frames
    # Training and Testing at DT
    # CLustering
    ## LDA
    
#########################################    
    
    
## ATTENTION READER...
##
## First, you will need to go to 
## https://newsapi.org/
## https://newsapi.org/register
## and get an API key

 

################## DO NOT USE MY KEY!!
## Get your own key. 
##
###################################################


### API KEY  - get a key!
##https://newsapi.org/

## Example URL
## https://newsapi.org/v2/everything?
## q=tesla&from=2021-05-20&sortBy=publishedAt&
## apiKey=YOUR KEY HERE


## What to import
import requests  ## for getting data from a server GET
import re   ## for regular expressions
import pandas as pd    ## for dataframes and related
from pandas import DataFrame

## To tokenize and vectorize text type data
from sklearn.feature_extraction.text import CountVectorizer
import numpy as np


####################################
##
##  Step 1: Connect to the server
##          Send a query
##          Collect and clean the 
##          results
####################################

####################################################
##In the following loop, we will query thenewsapi servers
##for all the topic names in the list
## We will then build a large csv file 
## where each article is a row
##
## From there, we will convert this data
## into a labeled dataframe
## so we can train and then test our DT
## model
####################################################

####################################################
## Build the URL and GET the results
## NOTE: At the bottom of this code
## commented out, you will find a second
## method for doing the following. This is FYI.
####################################################

## This is the endpoint - the server and 
## location on the server where your data 
## will be retrieved from

## TEST FIRST!
## We are about to build this URL:
## https://newsapi.org/v2/everything?apiKey=8f4134f7d0de43b8b49f91e22100f22b&q=bitcoin

from pprint import pprint

topics=['"student loans"', '"tuition"', '"tuition crisis"', '"student loan forgiveness"', 'cost of "higher education"']
# converting my exact match queries into simple labels
#labels = {'"charter school"':"charter", '"public school"': "public"}
labels = {}
for topic in topics:
    labels[topic] = topic

endpoint="https://newsapi.org/v2/everything"

# will hold my two resulting JSON structures with labels
results = {}

# hold a list of URLs to prevent multiple queries from adding the same article
urls = []

## topics needs to be a list of strings (words)
## Next, let's build the csv file
## first and add the column names
## Create a new csv file to save the headlines
filename="NewHeadlines.csv"
MyFILE=open(filename,"w")  # "a"  for append   "r" for read
## with open
### Place the column names in - write to the first row
WriteThis="LABEL,Date,Source,Title,Description,Content,URL\n"
MyFILE.write(WriteThis)
MyFILE.close()

## CHeck it! Can you find this file?
    
#### --------------------> GATHER - CLEAN - CREATE FILE    

## RE: documentation and options
## https://newsapi.org/docs/endpoints/everything

endpoint="https://newsapi.org/v2/everything"

################# enter for loop to collect
################# data on three topics
#######################################

for topic in topics:

    ## Dictionary Structure
    URLPost = {'apiKey':'961b4631b5af4e6e8f48ce780572befc',
               'q':topic,
               'searchIn': 'title,description',
               'sortBy': 'relevancy'
    }

    response=requests.get(endpoint, URLPost)
    print(response)
    jsontxt = response.json()
    pprint(jsontxt)
    
    # results dictionary -> maps label for topic to JSON result
    results[labels[topic]] = jsontxt
    pprint(results)
    #####################################################
    
    
    ## Open the file for append
    MyFILE=open(filename, "a")
    LABEL=topic
    for items in jsontxt["articles"]:
        print(items, "\n\n\n")
                  
        #Author=items["author"]
        #Author=str(Author)
        #Author=Author.replace(',', '')
        url = items["url"]

        # skips article if we've already written it
        if url not in urls:
            urls.append(url)
            Source=items["source"]["name"]
            print(Source)
            
            Date=items["publishedAt"]
            ##clean up the date
            NewDate=Date.split("T")
            Date=NewDate[0]
            print(Date)
            
            ## CLEAN the Title
            ##----------------------------------------------------------
            ##Replace punctuation with space
            # Accept one or more copies of punctuation         
            # plus zero or more copies of a space
            # and replace it with a single space
            Title=items["title"]
            Title=str(Title)
            #print(Title)
            Title=re.sub(r'[,.;@#?!&$\-\']+', ' ', str(Title), flags=re.IGNORECASE)
            Title=re.sub(' +', ' ', str(Title), flags=re.IGNORECASE)
            Title=re.sub(r'\"', ' ', str(Title), flags=re.IGNORECASE)
            
            # and replace it with a single space
            ## NOTE: Using the "^" on the inside of the [] means
            ## we want to look for any chars NOT a-z or A-Z and replace
            ## them with blank. This removes chars that should not be there.
            Title=re.sub(r'[^a-zA-Z]', " ", str(Title), flags=re.VERBOSE)
            Title=Title.replace(',', '')
            Title=' '.join(Title.split())
            Title=re.sub("\n|\r", "", Title)
            print(Title)
            ##----------------------------------------------------------
            
            Headline=items["description"]
            Headline=str(Headline)
            Headline=re.sub(r'[,.;@#?!&$\-\']+', ' ', Headline, flags=re.IGNORECASE)
            Headline=re.sub(' +', ' ', Headline, flags=re.IGNORECASE)
            Headline=re.sub(r'\"', ' ', Headline, flags=re.IGNORECASE)
            Headline=re.sub(r'[^a-zA-Z]', " ", Headline, flags=re.VERBOSE)
            ## Be sure there are no commas in the headlines or it will
            ## write poorly to a csv file....
            Headline=Headline.replace(',', '')
            Headline=' '.join(Headline.split())
            Headline=re.sub("\n|\r", "", Headline)
            
            ### AS AN OPTION - remove words of a given length............
            #Headline = ' '.join([wd for wd in Headline.split() if len(wd)>3])
        
            #print("Author: ", Author, "\n")
            #print("Title: ", Title, "\n")
            #print("Headline News Item: ", Headline, "\n\n")
            ##----------------------------------------------------------
            
            content=items["content"]
            content=str(content)
            content=re.sub(r'[,.;@#?!&$\-\']+', ' ', content, flags=re.IGNORECASE)
            content=re.sub(' +', ' ', content, flags=re.IGNORECASE)
            content=re.sub(r'\"', ' ', content, flags=re.IGNORECASE)
            content=re.sub(r'[^a-zA-Z]', " ", content, flags=re.VERBOSE)
            ## Be sure there are no commas in the headlines or it will
            ## write poorly to a csv file....
            content=content.replace(',', '')
            content=' '.join(content.split())
            content=re.sub("\n|\r", "", content)
            
        
            #print(Author)
            print(Title)
            print(Headline)
            
            WriteThis=str(LABEL)+","+str(Date)+","+str(Source)+","+ str(Title) + "," + str(Headline) + "," + str(content) + "," + str(items["url"]) + "\n"
            print(WriteThis)
            
            MyFILE.write(WriteThis)
        
    ## CLOSE THE FILE
    MyFILE.close()
    


<Response [200]>
{'articles': [{'author': 'Dashia Milden',
               'content': 'The Trump-Vance administration has issued a freeze '
                          'on federal loans and grants starting today, leaving '
                          'many wondering what this means for their federal '
                          'student financial aid.\r\n'
                          'A memo ordering the hal… [+1543 chars]',
               'description': 'The federal pause does not affect federal '
                              'student loans or Pell Grants, but its impact on '
                              'other student aid programs remains unclear.',
               'publishedAt': '2025-01-28T19:40:00Z',
               'source': {'id': None, 'name': 'CNET'},
               'title': 'What Happens to Student Loans and Financial Aid '
                        "During Trump's Federal Funding Freeze?",
               'url': 'https://www.cnet.com/personal-finance/loans/what-happens-to-student-loans

In [ ]:
################## END for loop

####################################################
##
## Where are we now?
## 
## So far, we have created a csv file
## with labeled data. Each row is a news article
##
## - BUT - 
## We are not done. We need to choose which
## parts of this data to use to model our decision tree
## and we need to convert the data into a data frame.
##
########################################################


BBC_DF=pd.read_csv(filename)
print(BBC_DF.head())
# iterating the columns 
for col in BBC_DF.columns: 
    print(col) 
    
print(BBC_DF["Content"])

## REMOVE any rows with NaN in them
BBC_DF = BBC_DF.dropna()
print(BBC_DF["Content"])

### Tokenize and Vectorize the Headlines
## Create the list of headlines
## Keep the labels!

HeadlineLIST=[]
LabelLIST=[]

for nexthead, nextlabel in zip(BBC_DF["Content"], BBC_DF["LABEL"]):
    HeadlineLIST.append(nexthead)
    LabelLIST.append(nextlabel)

print("The headline list is:\n")
print(HeadlineLIST)

print("The label list is:\n")
print(LabelLIST)


##########################################
## Remove all words that match the topics.
## For example, if the topics are food and covid
## remove these exact words.
##
## We will need to do this by hand. 
NewHeadlineLIST=[]

for element in HeadlineLIST:
    print(element)
    print(type(element))
    ## make into list
    AllWords=element.split(" ")
    print(AllWords)
    
    ## Now remove words that are in your topics
    NewWordsList=[]
    for word in AllWords:
        print(word)
        word=word.lower()
        if word in topics:
            print(word)
        else:
            NewWordsList.append(word)
            
    ##turn back to string
    NewWords=" ".join(NewWordsList)
    ## Place into NewHeadlineLIST
    NewHeadlineLIST.append(NewWords)


##
## Set the     HeadlineLIST to the new one
HeadlineLIST=NewHeadlineLIST
print(HeadlineLIST)     
#########################################
##
##  Build the labeled dataframe
##
######################################################

### Vectorize
## Instantiate your CV
MyCountV=CountVectorizer(
        input="Content",  ## because we have a csv file
        lowercase=True, 
        stop_words = "english",
        max_features=50
        )

## Use your CV 
MyDTM = MyCountV.fit_transform(HeadlineLIST)  # create a sparse matrix
print(type(MyDTM))


ColumnNames=MyCountV.get_feature_names_out()
#print(type(ColumnNames))


## Build the data frame
MyDTM_DF=pd.DataFrame(MyDTM.toarray(),columns=ColumnNames)

## Convert the labels from list to df
Labels_DF = DataFrame(LabelLIST,columns=['LABEL'])

## Check your new DF and you new Labels df:
print("Labels\n")
print(Labels_DF)
print("News df\n")
print(MyDTM_DF.iloc[:,0:6])

##Save original DF - without the lables
My_Orig_DF=MyDTM_DF
print(My_Orig_DF)
######################
## AND - just to make sure our dataframe is fair
## let's remove columns called:
## food, bitcoin, and sports (as these are label names)
######################
#MyDTM_DF=MyDTM_DF.drop(topics, axis=1)


## Now - let's create a complete and labeled
## dataframe:
dfs = [Labels_DF, MyDTM_DF]
print(dfs)

Final_News_DF_Labeled = pd.concat(dfs,axis=1, join='inner')
## DF with labels
print(Final_News_DF_Labeled)

 

 

#############################################
##
## Create Training and Testing Data
##
## Then model and test the Decision Tree
##
################################################


## Before we start our modeling, let's visualize and
## explore.

##It might be very interesting to see the word clouds 
## for each  of the topics. 
##--------------------------------------------------------
List_of_WC=[]

for mytopic in topics:

    tempdf = Final_News_DF_Labeled[Final_News_DF_Labeled['LABEL'] == mytopic]
    print(tempdf)
    
    tempdf =tempdf.sum(axis=0,numeric_only=True)
    #print(tempdf)
    
    #Make var name
    NextVarName=str("wc"+str(mytopic))
    #print( NextVarName)
    
    ##In the same folder as this code, I have three images
    ## They are called: food.jpg, bitcoin.jpg, and sports.jpg
    #next_image=str(str(mytopic) + ".jpg")
    #print(next_image)
    
    ## https://amueller.github.io/word_cloud/generated/wordcloud.WordCloud.html
    
    ###########
    ## Create and store in a list the wordcloud OBJECTS
    #########
    NextVarName = WordCloud(width=1000, height=600, background_color="white",
                   min_word_length=4, #mask=next_image,
                   max_words=200).generate_from_frequencies(tempdf)
    
    ## Here, this list holds all three wordclouds I am building
    List_of_WC.append(NextVarName)
    

##------------------------------------------------------------------
print(List_of_WC)
##########
########## Create the wordclouds
##########
fig=plt.figure(figsize=(25, 25))
#figure, axes = plt.subplots(nrows=2, ncols=2)
NumTopics=len(topics)
for i in range(NumTopics):
    print(i)
    ax = fig.add_subplot(NumTopics,1,i+1)
    plt.imshow(List_of_WC[i], interpolation='bilinear')
    plt.axis("off")
    plt.savefig("NewClouds.pdf")
 

In [25]:
# webscraping for media bias leanings
from selenium import webdriver
import time

driver = webdriver.Chrome()

baselink = "https://www.allsides.com/media-bias/ratings?field_featured_bias_rating_value=All&field_news_source_type_tid["

#fulllink = baselink + str("&field_news_source_type_tid[".join([str(i)+"]="+str(i) for i in range(1,3)]))

driver.get(fulllink)


In [53]:
from bs4 import BeautifulSoup
import time
linkendings = ["center", "left", "leftcenter","right-center", "right","conspiracy","fake-news","pro-science","satire"]
leanings = {"center": "Center", "left": "Left", "leftcenter": "Left-Center","right-center":"Right-Center", "right":"Right","conspiracy":"Conspiracy","fake-news":"Fake News","pro-science":"Scientific","satire":"Satire"}
mysources = []
for leaning in linkendings:
    time.sleep(2)
    page = requests.get("https://mediabiasfactcheck.com/" + leaning + "/").text
    soup = BeautifulSoup(page)
    if leaning == "satire":
        div = soup.find("div", {"class": "entry-content"})
        sources = div.find_all("a")
    else:
        table = soup.find("table", {"id":"mbfc-table"})
        sources = table.find_all("a")
    sources

    for source in sources:
        print(source.text)

        iteminfo = {}
        title = source.text
        iteminfo["Source"] = title.split("(")[0].strip()
        iteminfo["Source URL"] = title.split("(")[-1].strip()[:-1]
        iteminfo["Leaning"] = leanings[leaning]
        iteminfo["Detailed Report"] = source.attrs["href"]
        print (iteminfo["Detailed Report"])
        mysources.append(iteminfo)


1stHeadlines (1stheadlines.com)
https://mediabiasfactcheck.com/1stheadlines-bias-and-credibility/
5Pillars (5pillarsuk.com)
https://mediabiasfactcheck.com/5pillars-bias-and-credibility/
9News – KUSA (9news.com)
https://mediabiasfactcheck.com/9news-kusa/
11 News – KKCO (nbc11news.com)
https://mediabiasfactcheck.com/11-news-kkco/
12 News KPNX (12news.com)
https://mediabiasfactcheck.com/12-news-kpnx/
13 News – WIBW (wibw.com)
https://mediabiasfactcheck.com/13-news-wibw/
20/20 Insight (2020insightllc.com)
https://mediabiasfactcheck.com/20-20-insight-bias-and-credibility/
23WIFR News (wifr.com)
https://mediabiasfactcheck.com/23wifr-news/
24/7 Wall St. (247wallst.com)
https://mediabiasfactcheck.com/24-7-wall-st/
24ur.com
https://mediabiasfactcheck.com/24ur-com/
247sports (247sports.com)
https://mediabiasfactcheck.com/247sports-bias-and-credibility/
270toWin.com
https://mediabiasfactcheck.com/270towin-bias-and-credibility/
38 North (www.38north.org)
https://mediabiasfactcheck.com/38-north/
10

In [140]:
mysources = [source for source in mysources if "addtoany" not in source["Detailed Report"]]

mysources = [source for source in mysources if source["Source"][:-1] != source["Source URL"]]

df = pd.DataFrame(mysources)
df.sort_values("Source").reset_index().drop("index", axis=1)

Source               Source URL      Leaning  \
0     100 Days in Appalachia  100daysinappalachia.com  Left-Center   
1        100 Mile Free Press     100milefreepress.net  Left-Center   
2                100% Fed up      100percentfedup.com    Fake News   
3               1010 WINS AM       1010wins.radio.com       Center   
4             11 News – KKCO            nbc11news.com       Center   
...                      ...                      ...          ...   
7548                iPatriot             ipatriot.com    Fake News   
7549        iScience Journal       cell.com/iscience/   Scientific   
7550           openDemocracy    www.opendemocracy.net  Left-Center   
7551              zona.media                MediaZona         Left   
7552         Агрегатор 24СМИ            ex.24smi.info    Fake News   

                                        Detailed Report  
0     https://mediabiasfactcheck.com/100-days-in-app...  
1     https://mediabiasfactcheck.com/100-mile-free-p...  
2     https://mediabiasfactcheck.com/100-percent-fed...  
3          https://mediabiasfactcheck.com/1010-wins-am/  
4          https://mediabiasfactcheck.com/11-news-kkco/  
...                                                 ...  
7548           https://mediabiasfactcheck.com/ipatriot/  
7549  https://mediabiasfactcheck.com/iscience-journa...  
7550      https://mediabiasfactcheck.com/opendemocracy/  
7551    https://mediabiasfactcheck.com/zona-media-bias/  
7552  https://mediabiasfactcheck.com/%d0%b0%d0%b3%d1...  

[7553 rows x 4 columns]

In [141]:
sources = set()

articles = pd.read_csv("NewHeadlines.csv")
articles

for source in articles["Source"]:
    sources.add(source)

sources = list(sources)
rated_sources = list(df["Source"])
rated_source_urls = list(df["Source URL"])

import difflib
manual_matches = {"Breitbart News":"Breitbart","Freerepublic.com":"Free Republic"}

source_leanings = {}

for source in sources:
    title_matches = difflib.get_close_matches(source,rated_sources)
    url_matches = difflib.get_close_matches(source, rated_source_urls)
    source_leanings[source] = ""
    print(source, title_matches, url_matches)
    if source in manual_matches:
        source_leanings[source] = df[df["Source"] == manual_matches[source]].iloc[0]["Leaning"]
        
    else:
        if title_matches:
            if source.lower().split(".com")[0] == title_matches[0].lower().split(".com")[0]:
                source_leanings[source] = df[df["Source"] == title_matches[0]].iloc[0]["Leaning"]
                #print(source_leanings)
            else:
                no_the = source.lower().replace("the","").strip()
                title_matches = difflib.get_close_matches(no_the, rated_sources)
                no_spaces = no_the.replace(" ", "")
                if title_matches and no_the == title_matches[0].lower().split(".com")[0]:
                    source_leanings[source] = df[df["Source"] == title_matches[0]].iloc[0]["Leaning"]
            
                elif title_matches and no_spaces == title_matches[0].lower().split(".com")[0].replace(" ",""):
                    source_leanings[source] = df[df["Source"] == title_matches[0]].iloc[0]["Leaning"]
                
        if url_matches: 
            if source.lower().replace("www.","").replace(".com","") == url_matches[0].lower().replace("www.","").replace(".com",""):
                source_leanings[source] = df[df["Source URL"] == url_matches[0]].iloc[0]["Leaning"]
                #print(source_leanings)
    if source_leanings[source] == "":
        source_leanings[source] = "Not known"

CBS Sports ['Sunday Sport', 'Cell Reports', 'SGT Report'] []
The Times of India ['The Times of India', 'The Times of America', 'The Wire – India'] []
The Daily Dot ['The Daily Vox', 'Daily Dot', 'The Daily Star'] []
The Punch ['The Punch', 'The Sun', 'News Punch'] []
Common Dreams ['Common Dreams', 'Common Cause'] ['www.commondreams.org']
Teen Vogue ['Teen Vogue', 'The Voice'] ['teenvogue.com']
CNBC ['CNBC', 'MSNBC'] []
Yahoo Entertainment ['Now Entertainment', 'Entertainment Weekly', 'Valuetainment'] ['nowentertainment.net']
The Root ['The Root', 'The Dodo', 'The Recount'] []
Cheezburger.com [] ['theeagle.com', 'mecklenburgherald.com', 'hamburgreporter.com']
Www.gov.uk [] ['www.govtrack.us', 'www.lbc.co.uk']
Fox News ['Fox News', 'MxM News', '9 News'] ['Fake Fox News']
HYPEBEAST [] []
CNET ['CNET'] []
Memeorandum.com ['Memeorandum'] ['www.memeorandum.com', 'medium.com', 'keloland.com']
Fox17 [] []
Finextra ['Finextra'] ['finextra.com']
Slashdot.org ['Flashout'] ['acsh.org', 'glaad.org

In [129]:
articles["Source Leaning"] = articles["Source"].apply(lambda x: source_leanings[x])
articles.to_csv("NewHeadlines.csv")

In [93]:
import json
import requests
from pprint import pprint as pp2
 
#import os
#print os.getcwd()
 
#----------------------------------------------------------------------

print('begin log in')
#username and password
info = {"client_id":"menglert-text-mining","response_type":"code", "state":"freyapalooza", "redirect_uri":"https://www.reddit.com", "duration":"temporary","scope":"read"}
urlbase = "https://www.reddit.com/api/v1/authorize?" + "&".join([key + "=" + value for key,value in info.items()])
account = requests.get(urlbase)
print(account)
    #print r.text
    #print r.cookies
 
    #gets and saves the modhash
"""j = json.loads(r.text)
 
    client.modhash = j['json']['data']['modhash']
    print '{USER}\'s modhash is: {mh}'.format(USER=username, mh=client.modhash)
    client.user = username
    def name():
 
        return '{}\'s client'.format(username)
 
    #pp2(j)
 
    return client"""

begin log in
<Response [200]>


"j = json.loads(r.text)\n \n    client.modhash = j['json']['data']['modhash']\n    print '{USER}'s modhash is: {mh}'.format(USER=username, mh=client.modhash)\n    client.user = username\n    def name():\n \n        return '{}'s client'.format(username)\n \n    #pp2(j)\n \n    return client"

In [117]:
# !pip install PRAW
import praw
reddit = praw.Reddit(
    client_secret="j2rxzCvIBl6B1_EPb6U7701Wry25Jw",
    client_id="zBh3omUQnlmdmjucQVAWqQ",
    user_agent="menglert-text-mining (by u/menglert)",
    username="menglert",
    password="000174sme07"
)

url = "https://www.reddit.com/r/PoliticalDiscussion/comments/lij7jt/is_50000_of_student_debt_forgiveness_a_good_idea/"
submission = reddit.submission(url=url)


filename="RedditComments.csv"
MyFILE=open(filename,"w")  # "a"  for append   "r" for read
## with open
### Place the column names in - write to the first row
WriteThis="Source,ID,Comment,Parent,Score\n"
MyFILE.write(WriteThis)
MyFILE.close()

submission.comments.replace_more(limit=None)
for comment in submission.comments.list():
    MyFILE=open(filename,"a")
    content=str(comment.body)
    content=re.sub(r'[,.;@#?!&$\-]+', ' ', content, flags=re.IGNORECASE)
    content=re.sub(' +', ' ', content, flags=re.IGNORECASE)
    content=re.sub(r'\"', ' ', content, flags=re.IGNORECASE)
    content=re.sub(r'\'', '', content)
    content=re.sub(r'[^a-zA-Z]', " ", content, flags=re.VERBOSE)
    ## Be sure there are no commas in the headlines or it will
    ## write poorly to a csv file....
    content=content.replace(',', '')
    content=' '.join(content.split())
    content=re.sub("\n|\r", "", content)
    if content != "removed" and content != "deleted":
        WriteThis="Reddit,"+str(comment.id)+","+str(content)+","+ str(comment.parent_id) + ","+ str(comment.score) + "\n"
        #print(WriteThis)
        
        MyFILE.write(WriteThis)
    MyFILE.close()
    
    

In [105]:
submission.comments.replace_more(limit=None)
for comment in submission.comments.list():
    print(comment.body)

KeyboardInterrupt: 

In [143]:
submission.comments.replace_more(limit=None)
for comment in submission.comments.list():
    print(str(comment))

gn3er5i
gn46mmm
gn4u3km
gn4ob13
gn55nim
gn564x0
gn6aly9
gn4mqnu
gn4o46y
gn4qk3e
gn4qq7m
gn4eeju
gn4t66o
gn426d0
gn8jmjd
gn4ihdg
gn4hwks
gn4w75u
gn4om8c
gn4xzlk
gn9uo6c
gnahire
gn4ulu9
gn7pliz
gn9chr0
gna7ffr
gnbevey
gnbydwd
gn4ntxp
gn4hvc4
gn3fbxm
gn56mic
gn4v1zt
gn55zjv
gn4t88x
gn4urd6
gn50kel
gn6461v
gn9cq6d
gn4gc7w
gn560h2
gn42xz2
gn4fyhx
gn4q1m4
gn4oaz0
gn52fky
gn49xwv
gn4up1q
gn4xxpz
gn5908r
gn5gzdb
gn5xolw
gn60g8i
gn65uw0
gn6o86w
gn6rc12
gn702ux
gn71775
gn7jexd
gn7rjl7
gn7vu83
gn80wai
gn82a5t
gn8pa6d
gn8tch9
gn8tdt9
gn8wtzu
gn93guz
gn94icq
gn979ye
gn9kgrv
gna6s2s
gna80xz
gna8jcv
gnb22rm
gnbke4j
gn4pxb2
gn4ty63
gn4iqqu
gn4y78z
gn4yshm
gn51luf
gn4ne37
gn4tqex
gn59u22
gn43bks
gn535nc
gn42xhp
gn4q18n
gn4qlvw
gn6afts
gn8rirb
gn9zic1
gn45v4d
gn4ewf4
gn4q8po
gn4f6qp
gn4nod3
gn4qz8t
gn4u4ph
gn4z90m
gn4zmoq
gn50i4m
gn4q4i1
gn4q5tx
gn4sb7r
gn4wjfq
gn4zrl1
gn566wp
gn5c6ys
gn6vcqd
gn6vf8a
gn7ysx2
gn9v39n
gn48s7p
gn4p5w1
gn72xif
gn4qfg0
gn4f5l8
gn4kybp
gn4xbs9
gn54u9i
gn577qd
gn5a3g2
gn6l6on


In [133]:
justtext = pd.read_csv("NewHeadlines.csv")
justtext["type"] = justtext["Source"].apply(lambda x: "news article")


def get_combined_text(df):
    combined_col = {}
    for i in range(len(df)):
        title, desc, cont = df.iloc[i][["Title", "Description","Content"]]
        combined = ""
        if pd.notnull(title):
            combined = title
        if desc != title and pd.notnull(desc):
            combined += desc
        if cont != title and cont != desc and pd.notnull(cont):
            combined += cont
        combined_col[i] = combined
    return combined_col
justtext["Combined"] = get_combined_text(justtext)
justtext = justtext.drop(["Unnamed: 0", "LABEL", "Date", "Title", "Description", "Content", "URL"],axis=1)
justtext.to_csv("textdata.csv")

In [138]:
justtext_reddit = pd.read_csv("RedditComments.csv")
justtext_reddit["type"] = justtext_reddit["Source"].apply(lambda x: "reddit comment")
justtext_reddit["Source Leaning"] = "Not known"
justtext_reddit["Combined"] = justtext_reddit["Comment"]
justtext_reddit = justtext_reddit.drop(["ID","Parent", "Score","Comment"],axis=1)
justtext_reddit

finaldf = pd.concat([justtext, justtext_reddit], axis=0)
finaldf.to_csv("combinedtextdata.csv")

In [177]:
newsDF=pd.read_csv("combinedtextdata.csv")
## remove any rows with NA
newsDF = newsDF.dropna(how='any',axis=0)  ## axis 0 is rowwise
#print(newsDF)
# Saving the labels
mySources = newsDF["Source"]
myLeanings = newsDF["Source Leaning"]
myTypes = newsDF["type"]

## Remove the labels from the DF
DF_noLabel= newsDF.drop(["Source", "Source Leaning", "type", "Unnamed: 0"], axis=1) 
print(DF_noLabel)
### BUILD the LIST that "content" in CountVectorizer will expect
MyList=[]  #empty list
for i in range(0,len(DF_noLabel)):
    description=DF_noLabel.iloc[i,0] # gets the description for whatever row we're on
    if pd.notnull(description):
        MyList.append(description)
from sklearn.feature_extraction.text import TfidfVectorizer
# Declaring Tfidf Vectorizer for CSV file
csvVect = TfidfVectorizer(input="content",max_features=1000, stop_words = "english")

CV = csvVect.fit_transform(MyList)
MyColumnNames=csvVect.get_feature_names_out()

# Creating data frame
VectorizedDF_Text=pd.DataFrame(CV.toarray(),columns=MyColumnNames)


LabeledCLEAN_DF=pd.concat([mySources, myLeanings, myTypes, VectorizedDF_Text],axis=1)
LabeledCLEAN_DF

                                               Combined
0     What Happens to Student Loans and Financial Ai...
1     I took on almost K in debt to attend an Ivy Le...
2     Student Loans Still Available After White Hous...
3     Student loans for millions of federal borrower...
4     People Say Their Student Loans Are Being Cance...
...                                                 ...
1311  I have some sympathies for children who get in...
1312  I am reading everything three times because no...
1313  I did the same If they live on campus they can...
1314  Youre right I should not have commented on the...
1315  Private and STATE universities take FEDERAL gr...

[1316 rows x 1 columns]


Source Source Leaning            type  ability  able  \
0                    CNET         Center    news article      0.0   0.0   
1        Business Insider    Left-Center    news article      0.0   0.0   
2                    Time      Not known    news article      0.0   0.0   
3        Business Insider    Left-Center    news article      0.0   0.0   
4     Yahoo Entertainment      Not known    news article      0.0   0.0   
...                   ...            ...             ...      ...   ...   
1311               Reddit      Not known  reddit comment      0.0   0.0   
1312               Reddit      Not known  reddit comment      0.0   0.0   
1313               Reddit      Not known  reddit comment      0.0   0.0   
1314               Reddit      Not known  reddit comment      0.0   0.0   
1315               Reddit      Not known  reddit comment      0.0   0.0   

      absolutely  absurd  academic    accept    access  ...  www  yeah  \
0            0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
1            0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
2            0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
3            0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
4            0.0     0.0       0.0  0.295999  0.273303  ...  0.0   0.0   
...          ...     ...       ...       ...       ...  ...  ...   ...   
1311         0.0     0.0       0.0  0.000000  0.111484  ...  0.0   0.0   
1312         0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
1313         0.0     0.0       0.0  0.194541  0.000000  ...  0.0   0.0   
1314         0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   
1315         0.0     0.0       0.0  0.000000  0.000000  ...  0.0   0.0   

          year  years  yes  york  young     youre   yr  zero  
0     0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
1     0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
2     0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
3     0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
4     0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
...        ...    ...  ...   ...    ...       ...  ...   ...  
1311  0.000000    0.0  0.0   0.0    0.0  0.177951  0.0   0.0  
1312  0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
1313  0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  
1314  0.145503    0.0  0.0   0.0    0.0  0.092303  0.0   0.0  
1315  0.000000    0.0  0.0   0.0    0.0  0.000000  0.0   0.0  

[1316 rows x 1003 columns]

In [184]:
import nltk
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer 
LEMMER = WordNetLemmatizer() 

from nltk.stem.porter import PorterStemmer
STEMMER=PorterStemmer()
def MY_STEMMER(str_input):
    words = re.sub(r"[^A-Za-z\-]", " ", str_input).lower().split()
    words = [STEMMER.stem(word) for word in words]
    return words

def MY_LEMMER(str_input):
    words = re.sub(r"[^A-Za-z\-]", " ", str_input).lower().split()
    words = [LEMMER.lemmatize(word) for word in words]
    return words
##---------------------
## Using Stemming and Lemming
##-------------------------------------
MyVect_STEM=CountVectorizer(input='content',
                        analyzer = 'word',
                        stop_words='english',
                        tokenizer=MY_LEMMER,
                        lowercase = True,
                        max_features=100
                        )

Vect_Stem = MyVect_STEM.fit_transform(MyList)
ColumnNames_s=MyVect_STEM.get_feature_names_out()
VectorizedDF_Text=pd.DataFrame(Vect_Stem.toarray(),columns=ColumnNames_s)

LabeledCLEAN_DF=pd.concat([mySources, myLeanings, myTypes, VectorizedDF_Text],axis=1)
LabeledCLEAN_DF

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/menglert/nltk_data...
/Users/menglert/anaconda3/lib/python3.11/site-packages/sklearn/feature_extraction/text.py:525: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/Users/menglert/anaconda3/lib/python3.11/site-packages/sklearn/feature_extraction/text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['ha', 'le', 'u', 'wa'] not in stop_words.
  warnings.warn(


Source Source Leaning            type  administration  aid  \
0                    CNET         Center    news article               1    3   
1        Business Insider    Left-Center    news article               0    0   
2                    Time      Not known    news article               0    1   
3        Business Insider    Left-Center    news article               1    1   
4     Yahoo Entertainment      Not known    news article               0    0   
...                   ...            ...             ...             ...  ...   
1311               Reddit      Not known  reddit comment               1    0   
1312               Reddit      Not known  reddit comment               0    0   
1313               Reddit      Not known  reddit comment               0    0   
1314               Reddit      Not known  reddit comment               0    0   
1315               Reddit      Not known  reddit comment               0    0   

      american  average  benefit  better  biden  ...  trump  tuition  u  \
0            0        0        0       0      0  ...      2        0  0   
1            0        0        0       0      0  ...      0        0  1   
2            0        0        0       0      0  ...      0        0  0   
3            0        0        0       0      0  ...      4        0  0   
4            0        0        0       0      0  ...      0        0  0   
...        ...      ...      ...     ...    ...  ...    ...      ... ..   
1311         0        0        0       0      0  ...      0        0  0   
1312         0        0        0       1      0  ...      0        0  0   
1313         0        0        0       0      0  ...      0        1  0   
1314         0        0        0       0      0  ...      0        0  0   
1315         0        0        0       0      0  ...      0        0  0   

      university  wa  want  way  work  year  youre  
0              0   0     0    0     0     0      0  
1              2   0     0    0     0     0      0  
2              0   0     0    0     0     0      0  
3              0   0     0    0     0     0      0  
4              0   0     0    0     0     0      0  
...          ...  ..   ...  ...   ...   ...    ...  
1311           0   0     0    0     0     0      2  
1312           1   0     0    0     0     0      0  
1313           0   0     0    0     1     0      0  
1314           1   1     3    1     1     2      1  
1315           3   0     0    1     0     0      0  

[1316 rows x 103 columns]